In [2]:
from __future__ import print_function
import argparse
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torchvision import datasets, transforms
import numpy as np
import torch.utils.data as utils
import librosa
import soundfile as sf
import time
import os

In [3]:
sampleSize=16000#the length of the sample size
sample_rate=16000#the length of audio for one second
quantization_channels=256 #discretize the value to 256 numbers
#dilations=[2**i for i in range(8)]*20
#"residualDim=32
dilations=[2**i for i in range(9)]*5  #idea from wavenet, have more receptive field
residualDim=128 #
skipDim=512
shapeoftest = 190500
filterSize=3
resumefile='trypadmodel' # name of checkpoint
lossname='trypadlossfile.txt' # name of loss file
continueTrain=True # whether use checkpoint
pad = np.sum(dilations) # padding for dilate convolutional layers
lossrecord=[]  #list for record loss
#pad=0

    #            |----------------------------------------|     *residual*
    #            |                                        |
    #            |    |-- conv -- tanh --|                |
    # -> dilate -|----|                  * ----|-- 1x1 -- + -->	*input*
    #                 |-- conv -- sigm --|     |    ||
    #                                         1x1=residualDim
    #                                          |
    # ---------------------------------------> + ------------->	*skip=skipDim*
    image changed from https://github.com/vincentherrmann/pytorch-wavenet/blob/master/wavenet_model.py

In [3]:
#os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
#os.environ["CUDA_VISIBLE_DEVICES"] = "1"  # use specific GPU

In [4]:
use_cuda = torch.cuda.is_available() # whether have available GPU
torch.manual_seed(1)
device = torch.device("cuda" if use_cuda else "cpu")
#device = 'cpu'
torch.set_default_tensor_type('torch.cuda.FloatTensor') #set_default_tensor_type as cuda tensor
kwargs = {'num_workers': 1, 'pin_memory': True} if use_cuda else {} 

In [5]:
def mu_law_encode(audio, quantization_channels=quantization_channels,forX=False):
    '''Quantizes waveform amplitudes.'''
    mu = (quantization_channels - 1)*1.0
    # Perform mu-law companding transformation (ITU-T, 1988).
    # Minimum operation is here to deal with rare large amplitudes caused
    # by resampling.
    safe_audio_abs = np.minimum(np.abs(audio), 1.0)
    magnitude = np.log1p(mu * safe_audio_abs) / np.log1p(mu)
    signal = np.sign(audio) * magnitude
    # Quantize signal to the specified number of levels.
    if(forX):return signal
    return ((signal + 1) / 2 * mu + 0.5).astype(int) #discretize to 0~255
def mu_law_decode(output, quantization_channels=quantization_channels):
    '''Recovers waveform from quantized values.'''
    mu = quantization_channels - 1
    # Map values back to [-1, 1].
    signal = 2 * ((output*1.0) / mu) - 1
    # Perform inverse of mu-law transformation.
    magnitude = (1 / mu) * ((1 + mu)**np.abs(signal) - 1)
    return np.sign(signal) * magnitude
def onehot(a,mu=quantization_channels):
    b = np.zeros((a.shape[0], mu))
    b[np.arange(a.shape[0]), a] = 1
    return b

In [6]:
def readAudio(name):
    audio0, samplerate = sf.read(name, dtype='float32')
    return librosa.resample(audio0.T, samplerate, sample_rate).reshape(-1)
p=['./vsCorpus/origin_mix.wav','./vsCorpus/origin_vocal.wav',
   './vsCorpus/origin_mix.wav','./vsCorpus/origin_vocal.wav','./vsCorpus/pred_mix.wav']
xtrain,ytrain,xval,yval,xtest=readAudio(p[0]),readAudio(p[1]),readAudio(p[2]),readAudio(p[3]),readAudio(p[4])
assert((xtrain==xval).all())
assert((ytrain==yval).all())
assert((xtrain != ytrain).any())

In [7]:
ytrain,yval=mu_law_encode(ytrain),mu_law_encode(yval)
xtrain,xval,xtest=mu_law_encode(xtrain,forX=True),mu_law_encode(xval,forX=True),mu_law_encode(xtest,forX=True)
assert (xtrain.max()<=2 and ytrain.max() >= 5) 
#check whether testing set have been discretized but training set have not been discretized

In [8]:
'''xmean,xstd = xtrain.mean(),xtrain.std()
xtrain=(xtrain-xmean)/xstd
xval=(xval-xmean)/xstd
xtest=(xtest-xmean)/xstd'''

'xmean,xstd = xtrain.mean(),xtrain.std()\nxtrain=(xtrain-xmean)/xstd\nxval=(xval-xmean)/xstd\nxtest=(xtest-xmean)/xstd'

In [9]:
xtrain=np.pad(xtrain, (pad, pad), 'constant')  # padding for all audios
xval=np.pad(xval, (pad, pad), 'constant')
xtest=np.pad(xtest, (pad, pad), 'constant')
yval=np.pad(yval, (pad, pad), 'constant')
ytrain=np.pad(ytrain, (pad, pad), 'constant')

In [10]:
xtrain,xval,xtest=xtrain.reshape(1,1,-1),xval.reshape(1,1,-1),xtest.reshape(1,1,-1) 
ytrain,yval=ytrain.reshape(1,-1),yval.reshape(1,-1)
#reshape to 1 bathsize 1 depth and -1 length

In [11]:
xtrain,ytrain,xval,yval,xtest = torch.from_numpy(xtrain).type(torch.float32),\
                                torch.from_numpy(ytrain).type(torch.LongTensor),\
                                torch.from_numpy(xval).type(torch.float32),\
                                torch.from_numpy(yval).type(torch.LongTensor),\
                                torch.from_numpy(xtest).type(torch.float32)
#covert numpy array to torch tensor

In [12]:
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        sd,qd,rd = skipDim,quantization_channels,residualDim
        self.causal = nn.Conv1d(in_channels=1,out_channels=rd,kernel_size=3,padding=1)
        #normal cnn
        self.tanhconvs = nn.ModuleList()
        #please notice that you cannot use self.sigmoidconvs=dict(), otherwise the layers in the dict() can 
        #not update the weights
        self.sigmoidconvs = nn.ModuleList()
        self.skipconvs = nn.ModuleList()
        self.denseconvs = nn.ModuleList()
        for i, d in enumerate(dilations):
            self.tanhconvs.append(nn.Conv1d(in_channels=rd,out_channels=rd,kernel_size=3,padding=0,dilation=d))
            #1d cnn with dilation, if you don't know dilate
            #please check https://github.com/vdumoulin/conv_arithmetic/blob/master/README.md
            self.sigmoidconvs.append(nn.Conv1d(in_channels=rd,out_channels=rd,kernel_size=3,padding=0,dilation=d))
            self.skipconvs.append(nn.Conv1d(in_channels=rd,out_channels=sd,kernel_size=1))
            self.denseconvs.append(nn.Conv1d(in_channels=rd,out_channels=rd,kernel_size=1))
        self.post1 = nn.Conv1d(in_channels=sd,out_channels=sd,kernel_size=1)
        # normal cnn 
        self.post2 = nn.Conv1d(in_channels=sd,out_channels=qd,kernel_size=1)
        self.tanh,self.sigmoid = nn.Tanh(),nn.Sigmoid()

    def forward(self, x):
        finallen = x.shape[-1]-2*pad
        x = self.causal(x)#normal cnn
        for i, dilation in enumerate(dilations):
            xinput = x.clone()[:,:,dilation:-dilation]
            #when you do 1d cnn with dilation, and you do not padding, you need to do this
            x1 = self.tanh(self.tanhconvs[i](x))
            x2 = self.sigmoid(self.sigmoidconvs[i](x))
            x = x1*x2
            cutlen = (x.shape[-1] - finallen)//2
            if(i == 0):skip_connections= (self.skipconvs[i](x)).narrow(2,int(cutlen),int(finallen))
            else :skip_connections += (self.skipconvs[i](x)).narrow(2,int(cutlen),int(finallen))
            #inspired by resnet
            x = self.denseconvs[i](x)
            #fc 1d cnn kernel size =1
            x += xinput
        x = self.post2(F.relu(self.post1(F.relu(skip_connections))))
        return x

model = Net()#.cuda()
criterion = nn.CrossEntropyLoss()#.cuda()
#in wavenet paper, they said crossentropyloss is far better than MSELoss
#optimizer = optim.SGD(model.parameters(), lr=args.lr, momentum=args.momentum)
optimizer = optim.Adam(model.parameters(), lr=1e-3,weight_decay=1e-5)
#use adam to train
#optimizer = optim.SGD(model.parameters(), lr = 0.1, momentum=0.9, weight_decay=1e-4)
#scheduler = StepLR(optimizer, step_size=30, gamma=0.1)
#scheduler = MultiStepLR(optimizer, milestones=[20,40], gamma=0.1)

In [ ]:
if continueTrain:# if continueTrain, the program will find the checkpoints
    if os.path.isfile(resumefile):
        print("=> loading checkpoint '{}'".format(resumefile))
        checkpoint = torch.load(resumefile)
        start_epoch = checkpoint['epoch']
        #best_prec1 = checkpoint['best_prec1']
        model.load_state_dict(checkpoint['state_dict'])
        optimizer.load_state_dict(checkpoint['optimizer'])
        print("=> loaded checkpoint '{}' (epoch {})"
              .format(resumefile, checkpoint['epoch']))
    else:
        print("=> no checkpoint found at '{}'".format(resumefile))

In [15]:
def val(): #validation last 15 seconds of the audio.
    model.eval()
    startval_time = time.time()
    with torch.no_grad():
        idx = np.arange(xtrain.shape[-1]-pad-10*sampleSize,xtrain.shape[-1]-pad-sampleSize,1000)
        np.random.shuffle(idx)
        data = xtrain[:,:,idx[0]-pad:pad+idx[0]+sampleSize].to(device)
        target = ytrain[:,idx[0]:idx[0]+sampleSize].to(device)
        output = model(data)
        pred = output.max(1, keepdim=True)[1]
        correct = pred.eq(target.view_as(pred)).sum().item() / pred.shape[-1]
        val_loss = criterion(output, target).item()
        print(correct,'accurate')
        print('\nval set:loss{:.4f}:, ({:.3f} sec/step)\n'.format(val_loss,time.time()-startval_time))
        
        listofpred = []
        for ind in range(xtrain.shape[-1]-pad-10*sampleSize,xtrain.shape[-1]-pad-sampleSize,sampleSize):
            output = model(xtrain[:, :, ind - pad:ind + sampleSize + pad].to(device))
            pred = output.max(1, keepdim=True)[1].cpu().numpy().reshape(-1)
            listofpred.append(pred)
        ans = mu_law_decode(np.concatenate(listofpred))
        sf.write('./vsCorpus/notexval.wav', ans, sample_rate)
        

def test():# testing data
    model.eval()
    startval_time = time.time()
    with torch.no_grad():
        listofpred = []
        for ind in range(pad, xtest.shape[-1] - pad, sampleSize):
            output = model(xtest[:, :, ind - pad:ind + sampleSize + pad].to(device))
            pred = output.max(1, keepdim=True)[1].cpu().numpy().reshape(-1)
            listofpred.append(pred)
        ans = mu_law_decode(np.concatenate(listofpred))
        sf.write('./vsCorpus/notexte.wav', ans, sample_rate)

        listofpred=[]
        for ind in range(pad,xtrain.shape[-1]-pad,sampleSize):
            output = model(xtrain[:, :, ind-pad:ind+sampleSize+pad].to(device))
            pred = output.max(1, keepdim=True)[1].cpu().numpy().reshape(-1)
            listofpred.append(pred)
        ans = mu_law_decode(np.concatenate(listofpred))
        sf.write('./vsCorpus/notextr.wav', ans, sample_rate)
        print('stored done\n')
    
def train(epoch):
    model.train()
    idx = np.arange(pad,xtrain.shape[-1]-pad-sampleSize,8000)
    np.random.shuffle(idx)
    for i, ind in enumerate(idx):
        start_time = time.time()
        data, target = xtrain[:,:,ind-pad:ind+sampleSize+pad].to(device), ytrain[:,ind:ind+sampleSize].to(device)
        output = model(data)
        loss = criterion(output, target)
        lossrecord.append(loss.item())
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        print('Train Epoch: {} [{}/{} ({:.0f}%)] Loss:{:.6f}: , ({:.3f} sec/step)'.format(
                epoch, i, len(idx),100. * i / len(idx), loss.item(),time.time() - start_time))
        if i % 100 == 0:
            with open("./lossRecord/trypadlossfile.txt", "w") as f:
                for s in lossrecord:
                    f.write(str(s) +"\n")
            print('write finish')
            state={'epoch': epoch + 1,
                'state_dict': model.state_dict(),
                'optimizer': optimizer.state_dict()}
            torch.save(state, './model/'+resumefile)
    test()
    val()
def train(epoch):#training data, the audio except for last 15 seconds
    model.train()
    idx = np.arange(pad,xtrain.shape[-1]-pad-11*sampleSize,16000)
    np.random.shuffle(idx)#random the starting points
    for i, ind in enumerate(idx):
        start_time = time.time()
        data, target = xtrain[:,:,ind-pad:ind+sampleSize+pad].to(device), ytrain[:,ind:ind+sampleSize].to(device)
        output = model(data)
        loss = criterion(output, target)
        lossrecord.append(loss.item())
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        print('Train Epoch: {} [{}/{} ({:.0f}%)] Loss:{:.6f}: , ({:.3f} sec/step)'.format(
                epoch, i, len(idx),100. * i / len(idx), loss.item(),time.time() - start_time))
        if i % 100 == 0:
            with open("./lossRecord/"+lossname, "w") as f:
                for s in lossrecord:
                    f.write(str(s) +"\n")
            print('write finish')
            state={'epoch': epoch + 1,
                'state_dict': model.state_dict(),
                'optimizer': optimizer.state_dict()}
            torch.save(state, './model/'+resumefile)
    val()
    test()

In [16]:
for epoch in range(100000):
    train(epoch)
    test()

Train Epoch: 0 [0/470 (0%)] Loss:4.341933: , (1.201 sec/step)
write finish
Train Epoch: 0 [1/470 (0%)] Loss:4.321697: , (1.201 sec/step)
Train Epoch: 0 [2/470 (0%)] Loss:4.207393: , (1.199 sec/step)
Train Epoch: 0 [3/470 (1%)] Loss:4.030066: , (1.199 sec/step)
Train Epoch: 0 [4/470 (1%)] Loss:3.854748: , (1.198 sec/step)
Train Epoch: 0 [5/470 (1%)] Loss:4.296246: , (1.198 sec/step)
Train Epoch: 0 [6/470 (1%)] Loss:4.222650: , (1.197 sec/step)
Train Epoch: 0 [7/470 (1%)] Loss:4.054540: , (1.196 sec/step)
Train Epoch: 0 [8/470 (2%)] Loss:4.152524: , (1.196 sec/step)
Train Epoch: 0 [9/470 (2%)] Loss:4.155514: , (1.197 sec/step)
Train Epoch: 0 [10/470 (2%)] Loss:4.004141: , (1.196 sec/step)
Train Epoch: 0 [11/470 (2%)] Loss:4.447809: , (1.194 sec/step)
Train Epoch: 0 [12/470 (3%)] Loss:4.078428: , (1.197 sec/step)
Train Epoch: 0 [13/470 (3%)] Loss:4.145298: , (1.195 sec/step)
Train Epoch: 0 [14/470 (3%)] Loss:4.256442: , (1.200 sec/step)
Train Epoch: 0 [15/470 (3%)] Loss:4.208318: , (1.193

Train Epoch: 0 [129/470 (27%)] Loss:4.347756: , (1.198 sec/step)
Train Epoch: 0 [130/470 (28%)] Loss:4.744690: , (1.197 sec/step)
Train Epoch: 0 [131/470 (28%)] Loss:3.954391: , (1.196 sec/step)
Train Epoch: 0 [132/470 (28%)] Loss:4.062417: , (1.201 sec/step)
Train Epoch: 0 [133/470 (28%)] Loss:4.699494: , (1.204 sec/step)
Train Epoch: 0 [134/470 (29%)] Loss:4.224154: , (1.196 sec/step)
Train Epoch: 0 [135/470 (29%)] Loss:4.302280: , (1.194 sec/step)
Train Epoch: 0 [136/470 (29%)] Loss:4.529491: , (1.194 sec/step)
Train Epoch: 0 [137/470 (29%)] Loss:4.063563: , (1.194 sec/step)
Train Epoch: 0 [138/470 (29%)] Loss:4.213327: , (1.194 sec/step)
Train Epoch: 0 [139/470 (30%)] Loss:4.370289: , (1.193 sec/step)
Train Epoch: 0 [140/470 (30%)] Loss:4.159316: , (1.193 sec/step)
Train Epoch: 0 [141/470 (30%)] Loss:4.097656: , (1.193 sec/step)
Train Epoch: 0 [142/470 (30%)] Loss:4.402174: , (1.193 sec/step)
Train Epoch: 0 [143/470 (30%)] Loss:4.281171: , (1.193 sec/step)
Train Epoch: 0 [144/470 (

Train Epoch: 0 [255/470 (54%)] Loss:4.265447: , (1.196 sec/step)
Train Epoch: 0 [256/470 (54%)] Loss:4.570208: , (1.195 sec/step)
Train Epoch: 0 [257/470 (55%)] Loss:4.088964: , (1.195 sec/step)
Train Epoch: 0 [258/470 (55%)] Loss:4.057946: , (1.194 sec/step)
Train Epoch: 0 [259/470 (55%)] Loss:4.176943: , (1.195 sec/step)
Train Epoch: 0 [260/470 (55%)] Loss:3.752998: , (1.196 sec/step)
Train Epoch: 0 [261/470 (56%)] Loss:4.024511: , (1.194 sec/step)
Train Epoch: 0 [262/470 (56%)] Loss:4.371039: , (1.194 sec/step)
Train Epoch: 0 [263/470 (56%)] Loss:4.680456: , (1.195 sec/step)
Train Epoch: 0 [264/470 (56%)] Loss:4.004265: , (1.195 sec/step)
Train Epoch: 0 [265/470 (56%)] Loss:4.213607: , (1.196 sec/step)
Train Epoch: 0 [266/470 (57%)] Loss:4.047861: , (1.196 sec/step)
Train Epoch: 0 [267/470 (57%)] Loss:3.946784: , (1.194 sec/step)
Train Epoch: 0 [268/470 (57%)] Loss:4.188454: , (1.195 sec/step)
Train Epoch: 0 [269/470 (57%)] Loss:4.025015: , (1.195 sec/step)
Train Epoch: 0 [270/470 (

Train Epoch: 0 [381/470 (81%)] Loss:4.136870: , (1.199 sec/step)
Train Epoch: 0 [382/470 (81%)] Loss:4.325212: , (1.199 sec/step)
Train Epoch: 0 [383/470 (81%)] Loss:4.173262: , (1.200 sec/step)
Train Epoch: 0 [384/470 (82%)] Loss:4.426903: , (1.200 sec/step)
Train Epoch: 0 [385/470 (82%)] Loss:3.941491: , (1.200 sec/step)
Train Epoch: 0 [386/470 (82%)] Loss:4.351096: , (1.200 sec/step)
Train Epoch: 0 [387/470 (82%)] Loss:4.585780: , (1.199 sec/step)
Train Epoch: 0 [388/470 (83%)] Loss:4.012942: , (1.200 sec/step)
Train Epoch: 0 [389/470 (83%)] Loss:4.291359: , (1.200 sec/step)
Train Epoch: 0 [390/470 (83%)] Loss:3.809860: , (1.201 sec/step)
Train Epoch: 0 [391/470 (83%)] Loss:4.073983: , (1.201 sec/step)
Train Epoch: 0 [392/470 (83%)] Loss:4.508218: , (1.201 sec/step)
Train Epoch: 0 [393/470 (84%)] Loss:4.336500: , (1.201 sec/step)
Train Epoch: 0 [394/470 (84%)] Loss:3.965216: , (1.200 sec/step)
Train Epoch: 0 [395/470 (84%)] Loss:4.259925: , (1.200 sec/step)
Train Epoch: 0 [396/470 (

Train Epoch: 1 [37/470 (8%)] Loss:4.717124: , (1.194 sec/step)
Train Epoch: 1 [38/470 (8%)] Loss:3.986355: , (1.193 sec/step)
Train Epoch: 1 [39/470 (8%)] Loss:4.342321: , (1.193 sec/step)
Train Epoch: 1 [40/470 (9%)] Loss:4.349516: , (1.193 sec/step)
Train Epoch: 1 [41/470 (9%)] Loss:4.127096: , (1.194 sec/step)
Train Epoch: 1 [42/470 (9%)] Loss:4.472117: , (1.193 sec/step)
Train Epoch: 1 [43/470 (9%)] Loss:4.225720: , (1.194 sec/step)
Train Epoch: 1 [44/470 (9%)] Loss:4.370316: , (1.192 sec/step)
Train Epoch: 1 [45/470 (10%)] Loss:4.271725: , (1.194 sec/step)
Train Epoch: 1 [46/470 (10%)] Loss:4.273636: , (1.193 sec/step)
Train Epoch: 1 [47/470 (10%)] Loss:3.880467: , (1.195 sec/step)
Train Epoch: 1 [48/470 (10%)] Loss:4.345844: , (1.194 sec/step)
Train Epoch: 1 [49/470 (10%)] Loss:4.312946: , (1.195 sec/step)
Train Epoch: 1 [50/470 (11%)] Loss:4.027793: , (1.196 sec/step)
Train Epoch: 1 [51/470 (11%)] Loss:3.820653: , (1.196 sec/step)
Train Epoch: 1 [52/470 (11%)] Loss:3.954380: , (

...

Train Epoch: 125 [29/470 (6%)] Loss:1.243206: , (1.220 sec/step)
Train Epoch: 125 [30/470 (6%)] Loss:1.870052: , (1.220 sec/step)
Train Epoch: 125 [31/470 (7%)] Loss:1.453867: , (1.217 sec/step)
Train Epoch: 125 [32/470 (7%)] Loss:2.176568: , (1.221 sec/step)
Train Epoch: 125 [33/470 (7%)] Loss:1.973356: , (1.221 sec/step)
Train Epoch: 125 [34/470 (7%)] Loss:2.020846: , (1.219 sec/step)
Train Epoch: 125 [35/470 (7%)] Loss:1.512400: , (1.221 sec/step)
Train Epoch: 125 [36/470 (8%)] Loss:1.360543: , (1.218 sec/step)
Train Epoch: 125 [37/470 (8%)] Loss:1.300478: , (1.221 sec/step)
Train Epoch: 125 [38/470 (8%)] Loss:1.235424: , (1.221 sec/step)
Train Epoch: 125 [39/470 (8%)] Loss:2.734552: , (1.220 sec/step)
Train Epoch: 125 [40/470 (9%)] Loss:2.526095: , (1.240 sec/step)
Train Epoch: 125 [41/470 (9%)] Loss:1.997718: , (1.243 sec/step)
Train Epoch: 125 [42/470 (9%)] Loss:1.166229: , (1.242 sec/step)
Train Epoch: 125 [43/470 (9%)] Loss:2.661397: , (1.239 sec/step)
Train Epoch: 125 [44/470 

Train Epoch: 125 [153/470 (33%)] Loss:1.734108: , (1.220 sec/step)
Train Epoch: 125 [154/470 (33%)] Loss:1.427877: , (1.220 sec/step)
Train Epoch: 125 [155/470 (33%)] Loss:1.186095: , (1.221 sec/step)
Train Epoch: 125 [156/470 (33%)] Loss:2.687885: , (1.220 sec/step)
Train Epoch: 125 [157/470 (33%)] Loss:2.595561: , (1.219 sec/step)
Train Epoch: 125 [158/470 (34%)] Loss:2.154656: , (1.223 sec/step)
Train Epoch: 125 [159/470 (34%)] Loss:1.587613: , (1.234 sec/step)
Train Epoch: 125 [160/470 (34%)] Loss:1.222255: , (1.220 sec/step)
Train Epoch: 125 [161/470 (34%)] Loss:1.397142: , (1.219 sec/step)
Train Epoch: 125 [162/470 (34%)] Loss:1.399907: , (1.218 sec/step)
Train Epoch: 125 [163/470 (35%)] Loss:1.819908: , (1.216 sec/step)
Train Epoch: 125 [164/470 (35%)] Loss:1.855308: , (1.219 sec/step)
Train Epoch: 125 [165/470 (35%)] Loss:1.506256: , (1.219 sec/step)
Train Epoch: 125 [166/470 (35%)] Loss:1.943041: , (1.219 sec/step)
Train Epoch: 125 [167/470 (36%)] Loss:1.621010: , (1.220 sec/s

Train Epoch: 125 [276/470 (59%)] Loss:1.914317: , (1.221 sec/step)
Train Epoch: 125 [277/470 (59%)] Loss:1.741233: , (1.219 sec/step)
Train Epoch: 125 [278/470 (59%)] Loss:1.443329: , (1.219 sec/step)
Train Epoch: 125 [279/470 (59%)] Loss:1.205896: , (1.218 sec/step)
Train Epoch: 125 [280/470 (60%)] Loss:1.521401: , (1.214 sec/step)
Train Epoch: 125 [281/470 (60%)] Loss:1.309297: , (1.216 sec/step)
Train Epoch: 125 [282/470 (60%)] Loss:1.350569: , (1.233 sec/step)
Train Epoch: 125 [283/470 (60%)] Loss:2.782546: , (1.235 sec/step)
Train Epoch: 125 [284/470 (60%)] Loss:1.701092: , (1.220 sec/step)
Train Epoch: 125 [285/470 (61%)] Loss:2.029575: , (1.221 sec/step)
Train Epoch: 125 [286/470 (61%)] Loss:1.719011: , (1.213 sec/step)
Train Epoch: 125 [287/470 (61%)] Loss:1.932902: , (1.218 sec/step)
Train Epoch: 125 [288/470 (61%)] Loss:1.493225: , (1.237 sec/step)
Train Epoch: 125 [289/470 (61%)] Loss:2.062649: , (1.221 sec/step)
Train Epoch: 125 [290/470 (62%)] Loss:1.680115: , (1.217 sec/s

Train Epoch: 125 [399/470 (85%)] Loss:2.282585: , (1.225 sec/step)
Train Epoch: 125 [400/470 (85%)] Loss:1.265149: , (1.223 sec/step)
write finish
Train Epoch: 125 [401/470 (85%)] Loss:2.604807: , (1.222 sec/step)
Train Epoch: 125 [402/470 (86%)] Loss:2.547651: , (1.218 sec/step)
Train Epoch: 125 [403/470 (86%)] Loss:1.866153: , (1.219 sec/step)
Train Epoch: 125 [404/470 (86%)] Loss:1.452512: , (1.220 sec/step)
Train Epoch: 125 [405/470 (86%)] Loss:1.650935: , (1.222 sec/step)
Train Epoch: 125 [406/470 (86%)] Loss:1.099105: , (1.219 sec/step)
Train Epoch: 125 [407/470 (87%)] Loss:1.572301: , (1.220 sec/step)
Train Epoch: 125 [408/470 (87%)] Loss:1.554893: , (1.222 sec/step)
Train Epoch: 125 [409/470 (87%)] Loss:2.083783: , (1.218 sec/step)
Train Epoch: 125 [410/470 (87%)] Loss:1.852068: , (1.219 sec/step)
Train Epoch: 125 [411/470 (87%)] Loss:1.526530: , (1.222 sec/step)
Train Epoch: 125 [412/470 (88%)] Loss:1.404710: , (1.221 sec/step)
Train Epoch: 125 [413/470 (88%)] Loss:1.875588: ,

KeyboardInterrupt: 